# Transform IUPAC names into numerical data. Dopamine D1 receptor antagonists.

In [1]:
import pandas as pd

# Upload dataset as data frame
df_cids =pd.read_csv('df3_targets.csv', index_col=[0])

# To avoid truncation of some columns during data frame display
pd.set_option('display.max_columns', None) 

# Display the data frame
print('Shape of the data frame: ', df_cids.shape)
df_cids.head()

Shape of the data frame:  (49997, 2)


UPAC  target
0  N-(2,4-difluorophenyl)-2-(4-pyridin-2-ylpipera...       0
1  N-benzyl-2-[7-methyl-3-(4-methylbenzoyl)-4-oxo...       0
2  N-(1,3-benzodioxol-5-yl)-1-(4,6-dimethylpyrimi...       1
3  N-[[[2-(4-cyanophenoxy)acetyl]amino]carbamothi...       1
4  [2-oxo-2-[(3-oxo-1-phenylbutan-2-yl)amino]ethy...       0

In [2]:
df_cids = df_cids.dropna()
df_cids.shape

(49997, 2)

In [3]:
df_cids = df_cids.drop_duplicates()
df_cids.shape

(49996, 2)

In [4]:
df_cids = df_cids[df_cids['UPAC'].notna()]
df_cids['UPAC'] = df_cids['UPAC'].astype('string') 
df_cids.dtypes

UPAC      string[python]
target             int64
dtype: object

In [5]:
# make a copy to use latter for connection aiwth smiles 
df_iupac_target = df_cids.copy()

In [6]:
# Obtain listo fo UPAC formulas provided in PubChem
UPAC_list = df_cids['UPAC'].to_list()

for item in UPAC_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N-(2,4-difluorophenyl)-2-(4-pyridin-2-ylpiperazin-1-yl)acetamide
N-benzyl-2-[7-methyl-3-(4-methylbenzoyl)-4-oxo-1,8-naphthyridin-1-yl]acetamide
N-(1,3-benzodioxol-5-yl)-1-(4,6-dimethylpyrimidin-2-yl)piperidine-4-carboxamide
N-[[[2-(4-cyanophenoxy)acetyl]amino]carbamothioyl]cyclopropanecarboxamide
[2-oxo-2-[(3-oxo-1-phenylbutan-2-yl)amino]ethyl] 3-(1,3-dioxo-3a,4,7,7a-tetrahydroisoindol-2-yl)propanoate


In [7]:
from string import digits

# Remove elements from UPAC formulas
dataset = []
for i in UPAC_list:
    # Replace simbols with a coma
    new_list = i.translate(str.maketrans({'[': ' , ', ']': ' , ', 
                                         '(': ' , ', ')' : ' , ',
                                         '-': ' , ', ';' : ' , '}))
    
    new_str = new_list.translate(str.maketrans('', '', digits))
    dataset.append(new_str)
dataset

for item in dataset[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N ,  , , , difluorophenyl ,  ,  ,  ,  , pyridin ,  , ylpiperazin ,  , yl , acetamide
N , benzyl ,  ,  ,  , methyl ,  ,  ,  , methylbenzoyl ,  ,  , oxo , , , naphthyridin ,  , yl , acetamide
N ,  , , , benzodioxol ,  , yl ,  ,  ,  , , , dimethylpyrimidin ,  , yl , piperidine ,  , carboxamide
N ,  ,  ,  ,  ,  ,  , cyanophenoxy , acetyl , amino , carbamothioyl , cyclopropanecarboxamide
 ,  , oxo ,  ,  ,  ,  , oxo ,  , phenylbutan ,  , yl , amino , ethyl ,   ,  , , , dioxo , a,,,a , tetrahydroisoindol ,  , yl , propanoate


In [8]:
# Convert the strings into list of strings
new_strings = []
for i in dataset:
    parsed_string = i.split(",")
    new_strings.append(parsed_string)
new_strings

for item in new_strings[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

['N ', '  ', ' ', ' ', ' difluorophenyl ', '  ', '  ', '  ', '  ', ' pyridin ', '  ', ' ylpiperazin ', '  ', ' yl ', ' acetamide']
['N ', ' benzyl ', '  ', '  ', '  ', ' methyl ', '  ', '  ', '  ', ' methylbenzoyl ', '  ', '  ', ' oxo ', ' ', ' ', ' naphthyridin ', '  ', ' yl ', ' acetamide']
['N ', '  ', ' ', ' ', ' benzodioxol ', '  ', ' yl ', '  ', '  ', '  ', ' ', ' ', ' dimethylpyrimidin ', '  ', ' yl ', ' piperidine ', '  ', ' carboxamide']
['N ', '  ', '  ', '  ', '  ', '  ', '  ', ' cyanophenoxy ', ' acetyl ', ' amino ', ' carbamothioyl ', ' cyclopropanecarboxamide']
[' ', '  ', ' oxo ', '  ', '  ', '  ', '  ', ' oxo ', '  ', ' phenylbutan ', '  ', ' yl ', ' amino ', ' ethyl ', '   ', '  ', ' ', ' ', ' dioxo ', ' a', '', '', 'a ', ' tetrahydroisoindol ', '  ', ' yl ', ' propanoate']


In [9]:
from functools import reduce
# Convert list of lists in one list 
new_list = reduce(lambda a, b: a + b, new_strings)

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N 
  
 
 
 difluorophenyl 


In [10]:
new_list = [s.replace(' ', '') for s in new_list]
for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N



difluorophenyl


In [11]:
# Print the muber of left strings after reduction
print (len (new_list))

884735


In [12]:
# remove duplicates
from collections import OrderedDict

new_list = list(OrderedDict.fromkeys(new_list)) 

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N

difluorophenyl
pyridin
ylpiperazin


In [13]:
# Remove one letter strings
new_list_columns = [x for x in new_list if len(x) >= 4]

for item in new_list_columns[:5]:   # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

difluorophenyl
pyridin
ylpiperazin
acetamide
benzyl


In [14]:
print (len (new_list_columns))

4931


In [15]:
new_list_columns.sort()
new_list_columns

['acenaphthyleno',
 'acetaldehyde',
 'acetamide',
 'acetamido',
 'acetamidoacetate',
 'acetamidoacetyl',
 'acetamidoadamantane',
 'acetamidoanilino',
 'acetamidobenzenesulfonate',
 'acetamidobenzoate',
 'acetamidobenzoyl',
 'acetamidobutanoylamino',
 'acetamidocyclopentanecarbonyl',
 'acetamidoethoxy',
 'acetamidoethyl',
 'acetamidoethylamino',
 'acetamidoethylcarbamoyl',
 'acetamidofuran',
 'acetamidohexyl',
 'acetamidomethyl',
 'acetamidonaphthalene',
 'acetamidophenoxy',
 'acetamidophenyl',
 'acetamidopropanoate',
 'acetamidopyrazin',
 'acetamidopyridin',
 'acetamidothiophen',
 'acetate',
 'aceticacid',
 'acetohydrazide',
 'acetonitrile',
 'acetyl',
 'acetylanilino',
 'acetylbenzoyl',
 'acetylhydrazinyl',
 'acetylhydrazinylidene',
 'acetylimino',
 'acetylindol',
 'acetyloxy',
 'acetyloxybenzoyl',
 'acetyloxyethyl',
 'acetyloxymethyl',
 'acetyloxyoct',
 'acetyloxyphenyl',
 'acetyloxypropylamino',
 'acetylphenoxy',
 'acetylphenyl',
 'acetylpiperazin',
 'acetylpiperazine',
 'acetylpipe

In [16]:
import numpy as np

dict_func_groups = dict.fromkeys(new_list_columns, 0)
dict_func_groups

{'acenaphthyleno': 0,
 'acetaldehyde': 0,
 'acetamide': 0,
 'acetamido': 0,
 'acetamidoacetate': 0,
 'acetamidoacetyl': 0,
 'acetamidoadamantane': 0,
 'acetamidoanilino': 0,
 'acetamidobenzenesulfonate': 0,
 'acetamidobenzoate': 0,
 'acetamidobenzoyl': 0,
 'acetamidobutanoylamino': 0,
 'acetamidocyclopentanecarbonyl': 0,
 'acetamidoethoxy': 0,
 'acetamidoethyl': 0,
 'acetamidoethylamino': 0,
 'acetamidoethylcarbamoyl': 0,
 'acetamidofuran': 0,
 'acetamidohexyl': 0,
 'acetamidomethyl': 0,
 'acetamidonaphthalene': 0,
 'acetamidophenoxy': 0,
 'acetamidophenyl': 0,
 'acetamidopropanoate': 0,
 'acetamidopyrazin': 0,
 'acetamidopyridin': 0,
 'acetamidothiophen': 0,
 'acetate': 0,
 'aceticacid': 0,
 'acetohydrazide': 0,
 'acetonitrile': 0,
 'acetyl': 0,
 'acetylanilino': 0,
 'acetylbenzoyl': 0,
 'acetylhydrazinyl': 0,
 'acetylhydrazinylidene': 0,
 'acetylimino': 0,
 'acetylindol': 0,
 'acetyloxy': 0,
 'acetyloxybenzoyl': 0,
 'acetyloxyethyl': 0,
 'acetyloxymethyl': 0,
 'acetyloxyoct': 0,
 'ac

In [17]:
# https://stackoverflow.com/questions/28056171/how-to-build-and-fill-pandas-dataframe-from-for-loop
import copy
import re
dataset = []
data = []
# new_strings = []

list_formulas = df_cids['UPAC'].to_list()
for formula in list_formulas:
    new_list = re.findall(r'\b\w{4,}\b', formula)
    for group in new_list:
        # working
        new_dict = copy.deepcopy(dict_func_groups)
        for ii in new_list:
            if ii in new_dict.keys():
                new_dict[ii] +=1
                    
    id = formula
    # Combine all new features in an array
    # arr =[id, new_dict.values()]
    dataset.append(new_dict.values())

In [18]:
# Create an "index" column with the corresponding index values
df_iupac_target['index'] = df_iupac_target.index

# Display df_similarity
print('Shape of df_iupac_target ', df_iupac_target.shape)
df_iupac_target.head() 

Shape of df_iupac_target  (49996, 3)


UPAC  target  index
0  N-(2,4-difluorophenyl)-2-(4-pyridin-2-ylpipera...       0      0
1  N-benzyl-2-[7-methyl-3-(4-methylbenzoyl)-4-oxo...       0      1
2  N-(1,3-benzodioxol-5-yl)-1-(4,6-dimethylpyrimi...       1      2
3  N-[[[2-(4-cyanophenoxy)acetyl]amino]carbamothi...       1      3
4  [2-oxo-2-[(3-oxo-1-phenylbutan-2-yl)amino]ethy...       0      4

In [19]:
df_func_groups = pd.DataFrame.from_dict(dataset,
                                        orient='columns',
                                        dtype=None, columns=None) 


df_func_groups.columns = new_list_columns
df_func_groups.head()

acenaphthyleno  acetaldehyde  acetamide  acetamido  acetamidoacetate  \
0               0             0          1          0                 0   
1               0             0          1          0                 0   
2               0             0          0          0                 0   
3               0             0          0          0                 0   
4               0             0          0          0                 0   

   acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                0                    0                 0   
1                0                    0                 0   
2                0                    0                 0   
3                0                    0                 0   
4                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidobutanoylamino  acetamidocyclopentanecarbonyl  acetamidoethoxy  \
0                       0                              0                0   
1                       0                              0                0   
2                       0                              0                0   
3                       0                              0                0   
4                       0                              0                0   

   acetamidoethyl  acetamidoethylamino  acetamidoethylcarbamoyl  \
0               0                    0                        0   
1               0                    0                        0   
2               0                    0                        0   
3               0                    0                        0   
4               0                    0                        0   

   acetamidofuran  acetamidohexyl  acetamidomethyl  acetamidonaphthalene  \
0               0               0                0                     0   
1               0               0                0                     0   
2               0               0                0                     0   
3               0               0                0                     0   
4               0               0                0                     0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  acetamidopyrazin  \
0                 0                0                    0                 0   
1                 0                0                    0                 0   
2                 0                0                    0                 0   
3                 0                0                    0                 0   
4                 0                0                    0                 0   

   acetamidopyridin  acetamidothiophen  acetate  aceticacid  acetohydrazide  \
0                 0                  0        0           0               0   
1                 0                  0        0           0               0   
2                 0                  0        0           0               0   
3                 0                  0        0           0               0   
4                 0                  0        0           0               0   

   acetonitrile  acetyl  acetylanilino  acetylbenzoyl  acetylhydrazinyl  \
0             0       0              0              0                 0   
1             0       0              0              0                 0   
2             0       0              0              0                 0   
3             0       1              0              0                 0   
4             0       0              0              0                 0   

   acetylhydrazinylidene  acetylimino  acetyli

In [20]:
# Create an "index" column with the corresponding index values
df_func_groups['index'] = df_func_groups.index

# Convert the index values into strings
# df_func_groups['index'] = df_func_groups['index'].astype(str)

# Display df_similarity
print('Shape of df_func_groups: ', df_func_groups.shape)
df_func_groups.head() 

Shape of df_func_groups:  (49996, 4932)


acenaphthyleno  acetaldehyde  acetamide  acetamido  acetamidoacetate  \
0               0             0          1          0                 0   
1               0             0          1          0                 0   
2               0             0          0          0                 0   
3               0             0          0          0                 0   
4               0             0          0          0                 0   

   acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                0                    0                 0   
1                0                    0                 0   
2                0                    0                 0   
3                0                    0                 0   
4                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidobutanoylamino  acetamidocyclopentanecarbonyl  acetamidoethoxy  \
0                       0                              0                0   
1                       0                              0                0   
2                       0                              0                0   
3                       0                              0                0   
4                       0                              0                0   

   acetamidoethyl  acetamidoethylamino  acetamidoethylcarbamoyl  \
0               0                    0                        0   
1               0                    0                        0   
2               0                    0                        0   
3               0                    0                        0   
4               0                    0                        0   

   acetamidofuran  acetamidohexyl  acetamidomethyl  acetamidonaphthalene  \
0               0               0                0                     0   
1               0               0                0                     0   
2               0               0                0                     0   
3               0               0                0                     0   
4               0               0                0                     0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  acetamidopyrazin  \
0                 0                0                    0                 0   
1                 0                0                    0                 0   
2                 0                0                    0                 0   
3                 0                0                    0                 0   
4                 0                0                    0                 0   

   acetamidopyridin  acetamidothiophen  acetate  aceticacid  acetohydrazide  \
0                 0                  0        0           0               0   
1                 0                  0        0           0               0   
2                 0                  0        0           0               0   
3                 0                  0        0           0               0   
4                 0                  0        0           0               0   

   acetonitrile  acetyl  acetylanilino  acetylbenzoyl  acetylhydrazinyl  \
0             0       0              0              0                 0   
1             0       0              0              0                 0   
2             0       0              0              0                 0   
3             0       1              0              0                 0   
4             0       0              0              0                 0   

   acetylhydrazinylidene  acetylimino  acetyli

In [21]:
# Add the new data frame df_similarity to the already existing df based on "index"
df = pd.merge(df_iupac_target,df_func_groups, on=['index'])

# Display df_similarity
print('Shape of df: ', df.shape)
df.head()

Shape of df:  (49995, 4934)


UPAC  target  index  \
0  N-(2,4-difluorophenyl)-2-(4-pyridin-2-ylpipera...       0      0   
1  N-benzyl-2-[7-methyl-3-(4-methylbenzoyl)-4-oxo...       0      1   
2  N-(1,3-benzodioxol-5-yl)-1-(4,6-dimethylpyrimi...       1      2   
3  N-[[[2-(4-cyanophenoxy)acetyl]amino]carbamothi...       1      3   
4  [2-oxo-2-[(3-oxo-1-phenylbutan-2-yl)amino]ethy...       0      4   

   acenaphthyleno  acetaldehyde  acetamide  acetamido  acetamidoacetate  \
0               0             0          1          0                 0   
1               0             0          1          0                 0   
2               0             0          0          0                 0   
3               0             0          0          0                 0   
4               0             0          0          0                 0   

   acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                0                    0                 0   
1                0                    0                 0   
2                0                    0                 0   
3                0                    0                 0   
4                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidobutanoylamino  acetamidocyclopentanecarbonyl  acetamidoethoxy  \
0                       0                              0                0   
1                       0                              0                0   
2                       0                              0                0   
3                       0                              0                0   
4                       0                              0                0   

   acetamidoethyl  acetamidoethylamino  acetamidoethylcarbamoyl  \
0               0                    0                        0   
1               0                    0                        0   
2               0                    0                        0   
3               0                    0                        0   
4               0                    0                        0   

   acetamidofuran  acetamidohexyl  acetamidomethyl  acetamidonaphthalene  \
0               0               0                0                     0   
1               0               0                0                     0   
2               0               0                0                     0   
3               0               0                0                     0   
4               0               0                0                     0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  acetamidopyrazin  \
0                 0                0                    0                 0   
1                 0                0                    0                 0   
2                 0                0                    0                 0   
3                 0                0                    0                 0   
4                 0                0                    0                 0   

   acetamidopyridin  acetamidothiophen  acetate  aceticacid  acetohydrazide  \
0                 0                  0        0           0               0   
1                 0                  0        0           0               0   
2                 0                  0        0           0               0   
3                 0                  0        0           0               0   
4                 0                  0        0           0               0   

   acetonitrile  acetyl  acetylanilino  acetylbenzoyl  acetylhydrazinyl  \
0             0       0              0  

In [22]:
df.to_csv('df3_for_final.csv')

In [23]:
# Drop the CID and UPAC columns by name
df = df.drop(columns=['UPAC', 'index'],axis=1) 

In [24]:
# Display the data frame
print('Shape of the data frame: ', df.shape)
df.head()

Shape of the data frame:  (49995, 4932)


target  acenaphthyleno  acetaldehyde  acetamide  acetamido  \
0       0               0             0          1          0   
1       0               0             0          1          0   
2       1               0             0          0          0   
3       1               0             0          0          0   
4       0               0             0          0          0   

   acetamidoacetate  acetamidoacetyl  acetamidoadamantane  acetamidoanilino  \
0                 0                0                    0                 0   
1                 0                0                    0                 0   
2                 0                0                    0                 0   
3                 0                0                    0                 0   
4                 0                0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidobutanoylamino  acetamidocyclopentanecarbonyl  acetamidoethoxy  \
0                       0                              0                0   
1                       0                              0                0   
2                       0                              0                0   
3                       0                              0                0   
4                       0                              0                0   

   acetamidoethyl  acetamidoethylamino  acetamidoethylcarbamoyl  \
0               0                    0                        0   
1               0                    0                        0   
2               0                    0                        0   
3               0                    0                        0   
4               0                    0                        0   

   acetamidofuran  acetamidohexyl  acetamidomethyl  acetamidonaphthalene  \
0               0               0                0                     0   
1               0               0                0                     0   
2               0               0                0                     0   
3               0               0                0                     0   
4               0               0                0                     0   

   acetamidophenoxy  acetamidophenyl  acetamidopropanoate  acetamidopyrazin  \
0                 0                0                    0                 0   
1                 0                0                    0                 0   
2                 0                0                    0                 0   
3                 0                0                    0                 0   
4                 0                0                    0                 0   

   acetamidopyridin  acetamidothiophen  acetate  aceticacid  acetohydrazide  \
0                 0                  0        0           0               0   
1                 0                  0        0           0               0   
2                 0                  0        0           0               0   
3                 0                  0        0           0               0   
4                 0                  0        0           0               0   

   acetonitrile  acetyl  acetylanilino  acetylbenzoyl  acetylhydrazinyl  \
0             0       0              0              0                 0   
1             0       0              0              0                 0   
2             0       0              0              0                 0   
3             0       1              0              0                 0   
4             0       0              0              0                 0   

In [25]:
df.to_csv('df3_targets_IUPACs.csv')